In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/mydata/test_data/test_data/test_open/s0032_03166_0_0_1_1_0_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0032_00902_0_1_1_2_1_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0025_00879_0_0_1_0_1_01.png
/kaggle/input/mydata/test_data/test_data/test_open/s0014_08315_0_0_1_1_0_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0012_08605_0_0_1_1_0_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0037_09301_1_1_1_2_0_01.png
/kaggle/input/mydata/test_data/test_data/test_open/s0012_08321_0_0_1_0_0_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0019_04192_0_0_1_0_1_01.png
/kaggle/input/mydata/test_data/test_data/test_open/s0032_02719_0_1_1_2_1_02.png
/kaggle/input/mydata/test_data/test_data/test_open/s0022_00163_0_0_1_0_1_01.png
/kaggle/input/mydata/test_data/test_data/test_open/s0036_04800_1_0_1_0_1_01.png
/kaggle/input/mydata/test_data/test_data/test_open/s0036_03473_1_0_1_0_0_01.png
/kaggle/input/mydata/test_data/test_data

In [2]:
import tensorflow as tf
from tensorflow.keras.applications import InceptionV3
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dropout,Input,Flatten,Dense,MaxPooling2D
from tensorflow.keras.preprocessing.image import ImageDataGenerator  # Data Augumentation

In [3]:
batchsize=8

In [4]:
train_datagen= ImageDataGenerator(rescale=1./255, rotation_range=0.2,shear_range=0.2,
    zoom_range=0.2,width_shift_range=0.2,
    height_shift_range=0.2, validation_split=0.2)

train_data= train_datagen.flow_from_directory('/kaggle/input/mydata/train_data/train_data',
                                target_size=(80,80),batch_size=batchsize,class_mode='categorical',subset='training' )

validation_data= train_datagen.flow_from_directory('/kaggle/input/mydata/train_data/train_data',
                                target_size=(80,80),batch_size=batchsize,class_mode='categorical', subset='validation')

Found 54336 images belonging to 2 classes.
Found 13583 images belonging to 2 classes.


In [5]:
test_datagen = ImageDataGenerator(rescale=1./255)

test_data = test_datagen.flow_from_directory('/kaggle/input/mydata/test_data/test_data',
                                target_size=(80,80),batch_size=batchsize,class_mode='categorical')

Found 16979 images belonging to 2 classes.


In [6]:
bmodel = InceptionV3(include_top=False, weights='imagenet', input_tensor=Input(shape=(80,80,3)))
hmodel = bmodel.output
hmodel = Flatten()(hmodel)
hmodel = Dense(64, activation='relu')(hmodel)
hmodel = Dropout(0.5)(hmodel)
hmodel = Dense(2,activation= 'softmax')(hmodel)

model = Model(inputs=bmodel.input, outputs= hmodel)
for layer in bmodel.layers:
    layer.trainable = False

87910968/87910968 ━━━━━━━━━━━━━━━━━━━━ 0s 0us/step


In [7]:
model.summary()

Model: "functional"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┓
┃ Layer (type)              ┃ Output Shape           ┃        Param # ┃ Connected to           ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━┩
│ input_layer (InputLayer)  │ (None, 80, 80, 3)      │              0 │ -                      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d (Conv2D)           │ (None, 39, 39, 32)     │            864 │ input_layer[0][0]      │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization       │ (None, 39, 39, 32)     │             96 │ conv2d[0][0]           │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation (Activation)   │ (None, 39, 39, 32)     │              0 │ batch_normalization[0… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_1 (Conv2D)         │ (None, 37, 37, 32)     │          9,216 │ activation[0][0]       │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_1     │ (None, 37, 37, 32)     │             96 │ conv2d_1[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_1 (Activation) │ (None, 37, 37, 32)     │              0 │ batch_normalization_1… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_2 (Conv2D)         │ (None, 37, 37, 64)     │         18,432 │ activation_1[0][0]     │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_2     │ (None, 37, 37, 64)     │            192 │ conv2d_2[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_2 (Activation) │ (None, 37, 37, 64)     │              0 │ batch_normalization_2… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ max_pooling2d             │ (None, 18, 18, 64)     │              0 │ activation_2[0][0]     │
│ (MaxPooling2D)            │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_3 (Conv2D)         │ (None, 18, 18, 80)     │          5,120 │ max_pooling2d[0][0]    │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_3     │ (None, 18, 18, 80)     │            240 │ conv2d_3[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_3 (Activation) │ (None, 18, 18, 80)     │              0 │ batch_normalization_3… │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ conv2d_4 (Conv2D)         │ (None, 16, 16, 192)    │        138,240 │ activation_3[0][0]     │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ batch_normalization_4     │ (None, 16, 16, 192)    │            576 │ conv2d_4[0][0]         │
│ (BatchNormalization)      │                        │                │                        │
├───────────────────────────┼────────────────────────┼────────────────┼────────────────────────┤
│ activation_4 (Activat

 Total params: 21,934,050 (83.67 MB)

 Trainable params: 131,266 (512.76 KB)

 Non-trainable params: 21,802,784 (83.17 MB)

In [8]:
from tensorflow.keras.callbacks import ModelCheckpoint,EarlyStopping, ReduceLROnPlateau

In [9]:
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping, ReduceLROnPlateau

# Define the callback for saving the model weights
checkpoint = ModelCheckpoint(
    filepath='/kaggle/working/model.weights.h5',  # Correct extension for weights
    monitor='val_loss',
    save_best_only=True,
    save_weights_only=True,  # Save only the weights
    verbose=3
)

# Early stopping to prevent overfitting
earlystop = EarlyStopping(
    monitor='val_loss',
    patience=7,
    verbose=3,
    restore_best_weights=True
)

# Reduce learning rate on plateau
learning_rate = ReduceLROnPlateau(
    monitor='val_loss',
    patience=3,
    verbose=3
)

# Add callbacks
callbacks = [checkpoint, earlystop, learning_rate]


In [10]:
model.compile(optimizer='Adam', loss='categorical_crossentropy',metrics=['accuracy'])

model.fit(train_data,steps_per_epoch=train_data.samples//batchsize,
                   validation_data=validation_data,
                   validation_steps=validation_data.samples//batchsize,
                   callbacks=callbacks,
                    epochs=5)

Epoch 1/5


/usr/local/lib/python3.10/dist-packages/keras/src/trainers/data_adapters/py_dataset_adapter.py:121: UserWarning: Your `PyDataset` class should call `super().__init__(**kwargs)` in its constructor. `**kwargs` can include `workers`, `use_multiprocessing`, `max_queue_size`. Do not pass these arguments to `fit()`, as they will be ignored.
  self._warn_if_super_not_called()


6792/6792 ━━━━━━━━━━━━━━━━━━━━ 318s 45ms/step - accuracy: 0.9058 - loss: 0.2373 - val_accuracy: 0.9045 - val_loss: 0.2390 - learning_rate: 0.0010
Epoch 2/5


/usr/lib/python3.10/contextlib.py:153: UserWarning: Your input ran out of data; interrupting training. Make sure that your dataset or generator can generate at least `steps_per_epoch * epochs` batches. You may need to use the `.repeat()` function when building your dataset.
  self.gen.throw(typ, value, traceback)



Epoch 2: val_loss improved from 0.23898 to 0.11958, saving model to /kaggle/working/model.weights.h5
6792/6792 ━━━━━━━━━━━━━━━━━━━━ 5s 664us/step - accuracy: 0.0000e+00 - loss: 0.0000e+00 - val_accuracy: 1.0000 - val_loss: 0.1196 - learning_rate: 0.0010
Epoch 3/5
6791/6792 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - accuracy: 0.9298 - loss: 0.1806
Epoch 3: val_loss did not improve from 0.11958
6792/6792 ━━━━━━━━━━━━━━━━━━━━ 196s 29ms/step - accuracy: 0.9298 - loss: 0.1806 - val_accuracy: 0.8957 - val_loss: 0.2583 - learning_rate: 0.0010
Epoch 4/5

Epoch 4: val_loss improved from 0.11958 to 0.09462, saving model to /kaggle/working/model.weights.h5
6792/6792 ━━━━━━━━━━━━━━━━━━━━ 1s 106us/step - accuracy: 0.0000e+00 - loss: 0.0000e+00 - val_accuracy: 1.0000 - val_loss: 0.0946 - learning_rate: 0.0010
Epoch 5/5
6788/6792 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step - accuracy: 0.9350 - loss: 0.1704
Epoch 5: val_loss did not improve from 0.09462
6792/6792 ━━━━━━━━━━━━━━━━━━━━ 194s 28ms/step - accuracy: 0.9350

In [12]:
acc_tr, loss_tr = model.evaluate(train_data)
print(acc_tr)
print(loss_tr)

6792/6792 ━━━━━━━━━━━━━━━━━━━━ 153s 23ms/step - accuracy: 0.9415 - loss: 0.1514
0.15293212234973907
0.9411439895629883


In [13]:
acc_vr, loss_vr = model.evaluate(validation_data)
print(acc_vr)
print(loss_vr)

1698/1698 ━━━━━━━━━━━━━━━━━━━━ 38s 23ms/step - accuracy: 0.8975 - loss: 0.2610
0.26290470361709595
0.8988441228866577


In [14]:
acc_test, loss_test = model.evaluate(test_data)
print(acc_tr)
print(loss_tr)

2123/2123 ━━━━━━━━━━━━━━━━━━━━ 63s 30ms/step - accuracy: 0.9404 - loss: 0.1583
0.15293212234973907
0.9411439895629883


In [15]:
# Save your model
model.save('my_model.h5')

In [16]:
model.save('my_model.h5')
print("Model saved successfully")

# Also verify the file exists
import os
if os.path.exists('my_model.h5'):
    print("File exists at:", os.getcwd() + '/my_model.h5')

Model saved successfully
File exists at: /kaggle/working/my_model.h5


In [18]:
!zip -r zip_folder.zip my_model.h5

  adding: my_model.h5 (deflated 8%)


In [19]:
from IPython.display import FileLink

FileLink('zip_folder.zip')

/kaggle/working/zip_folder.zip